In [1]:
# Source: https://www.immersivelimit.com/tutorials/create-coco-annotations-from-scratch/#create-custom-coco-dataset
import base64
import IPython
import json
import numpy as np
import os
import random
import requests
from io import BytesIO
from math import trunc
from PIL import Image as PILImage
from PIL import ImageDraw as PILImageDraw


In [2]:
# Load the dataset json
class CocoDataset():
    def __init__(self, annotation_path, image_dir):
        self.annotation_path = annotation_path
        self.image_dir = image_dir
        self.colors = ['blue', 'purple', 'red', 'green', 'orange', 'salmon', 'pink', 'gold',
                        'orchid', 'slateblue', 'limegreen', 'seagreen', 'darkgreen', 'olive',
                        'teal', 'aquamarine', 'steelblue', 'powderblue', 'dodgerblue', 'navy',
                        'magenta', 'sienna', 'maroon']
        
        json_file = open(self.annotation_path)
        self.coco = json.load(json_file)
        json_file.close()
        
        #self.process_info()
        #self.process_licenses()
        self.process_categories()
        self.process_images()
        self.process_segmentations()

    def display_info(self):
        print('Dataset Info:')
        print('=============')
        for key, item in self.info.items():
            print('  {}: {}'.format(key, item))
        
        requirements = [['description', str],
                        ['url', str],
                        ['version', str],
                        ['year', int],
                        ['contributor', str],
                        ['date_created', str]]
        for req, req_type in requirements:
            if req not in self.info:
                print('ERROR: {} is missing'.format(req))
            elif type(self.info[req]) != req_type:
                print('ERROR: {} should be type {}'.format(req, str(req_type)))
        print('')
        
    def display_licenses(self):
        print('Licenses:')
        print('=========')
        
        requirements = [['id', int],
                        ['url', str],
                        ['name', str]]
        for license in self.licenses:
            for key, item in license.items():
                print('  {}: {}'.format(key, item))
            for req, req_type in requirements:
                if req not in license:
                    print('ERROR: {} is missing'.format(req))
                elif type(license[req]) != req_type:
                    print('ERROR: {} should be type {}'.format(req, str(req_type)))
            print('')
        print('')
        
    def display_categories(self):
        print('Categories:')
        print('=========')
        for sc_key, sc_val in self.super_categories.items():
            print('  super_category: {}'.format(sc_key))
            for cat_id in sc_val:
                print('    id {}: {}'.format(cat_id, self.categories[cat_id]['name']))
            print('')
    
    def display_image(self, image_id, show_polys=True, show_bbox=True, show_labels=True, show_crowds=True, use_url=False):
        print('Image:')
        print('======')
        if image_id == 'random':
            image_id = random.choice(list(self.images.keys()))
        
        # Print the image info
        image = self.images[image_id]
        for key, val in image.items():
            print('  {}: {}'.format(key, val))
            
        # Open the image
        if use_url:
            image_path = image['coco_url']
            response = requests.get(image_path)
            image = PILImage.open(BytesIO(response.content))
            
        else:
            image_path = os.path.join(self.image_dir, image['file_name'])
            image = PILImage.open(image_path)
            
        buffered = BytesIO()
        image.save(buffered, format="PNG")
        img_str = "data:image/png;base64, " + base64.b64encode(buffered.getvalue()).decode()
        
        # Calculate the size and adjusted display size
        max_width = 900
        image_width, image_height = image.size
        adjusted_width = min(image_width, max_width)
        adjusted_ratio = adjusted_width / image_width
        adjusted_height = adjusted_ratio * image_height
        
        # Create list of polygons to be drawn
        polygons = {}
        bbox_polygons = {}
        rle_regions = {}
        poly_colors = {}
        labels = {}
        print('  segmentations ({}):'.format(len(self.segmentations[image_id])))
        for i, segm in enumerate(self.segmentations[image_id]):
            polygons_list = []
            if segm['iscrowd'] != 0:
                # Gotta decode the RLE
                px = 0
                x, y = 0, 0
                rle_list = []
                for j, counts in enumerate(segm['segmentation']['counts']):
                    if j % 2 == 0:
                        # Empty pixels
                        px += counts
                    else:
                        # Need to draw on these pixels, since we are drawing in vector form,
                        # we need to draw horizontal lines on the image
                        x_start = trunc(trunc(px / image_height) * adjusted_ratio)
                        y_start = trunc(px % image_height * adjusted_ratio)
                        px += counts
                        x_end = trunc(trunc(px / image_height) * adjusted_ratio)
                        y_end = trunc(px % image_height * adjusted_ratio)
                        if x_end == x_start:
                            # This is only on one line
                            rle_list.append({'x': x_start, 'y': y_start, 'width': 1 , 'height': (y_end - y_start)})
                        if x_end > x_start:
                            # This spans more than one line
                            # Insert top line first
                            rle_list.append({'x': x_start, 'y': y_start, 'width': 1, 'height': (image_height - y_start)})
                            
                            # Insert middle lines if needed
                            lines_spanned = x_end - x_start + 1 # total number of lines spanned
                            full_lines_to_insert = lines_spanned - 2
                            if full_lines_to_insert > 0:
                                full_lines_to_insert = trunc(full_lines_to_insert * adjusted_ratio)
                                rle_list.append({'x': (x_start + 1), 'y': 0, 'width': full_lines_to_insert, 'height': image_height})
                                
                            # Insert bottom line
                            rle_list.append({'x': x_end, 'y': 0, 'width': 1, 'height': y_end})
                if len(rle_list) > 0:
                    rle_regions[segm['id']] = rle_list  
            else:
                # Add the polygon segmentation
                for segmentation_points in segm['segmentation']:
                    segmentation_points = np.multiply(segmentation_points, adjusted_ratio).astype(int)
                    polygons_list.append(str(segmentation_points).lstrip('[').rstrip(']'))

            polygons[segm['id']] = polygons_list

            if i < len(self.colors):
                poly_colors[segm['id']] = self.colors[i]
            else:
                poly_colors[segm['id']] = 'white'
            
            bbox = segm['bbox']
            bbox_points = [bbox[0], bbox[1], bbox[0] + bbox[2], bbox[1],
                           bbox[0] + bbox[2], bbox[1] + bbox[3], bbox[0], bbox[1] + bbox[3],
                           bbox[0], bbox[1]]
            bbox_points = np.multiply(bbox_points, adjusted_ratio).astype(int)
            bbox_polygons[segm['id']] = str(bbox_points).lstrip('[').rstrip(']')
            
            labels[segm['id']] = (self.categories[segm['category_id']]['name'], (bbox_points[0], bbox_points[1] - 4))
            
            # Print details
            print('    {}:{}:{}'.format(segm['id'], poly_colors[segm['id']], self.categories[segm['category_id']]))

        # Draw segmentation polygons on image
        html = '<div class="container" style="position:relative;">'
        html += '<img src="{}" style="position:relative;top:0px;left:0px;width:{}px;">'.format(img_str, adjusted_width)
        html += '<div class="svgclass"><svg width="{}" height="{}">'.format(adjusted_width, adjusted_height)
        
        if show_polys:
            for seg_id, points_list in polygons.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                for points in points_list:
                    html += '<polygon points="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0.5" />'.format(points, fill_color, stroke_color)
        
        if show_crowds:
            for seg_id, rect_list in rle_regions.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                for rect_def in rect_list:
                    x, y = rect_def['x'], rect_def['y']
                    w, h = rect_def['width'], rect_def['height']
                    html += '<rect x="{}" y="{}" width="{}" height="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0.5; stroke-opacity:0.5" />'.format(x, y, w, h, fill_color, stroke_color)
            
        if show_bbox:
            for seg_id, points in bbox_polygons.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                html += '<polygon points="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0" />'.format(points, fill_color, stroke_color)
                
        if show_labels:
            for seg_id, label in labels.items():
                color = poly_colors[seg_id]
                html += '<text x="{}" y="{}" style="fill:{}; font-size: 12pt;">{}</text>'.format(label[1][0], label[1][1], color, label[0])
                
        html += '</svg></div>'
        html += '</div>'
        html += '<style>'
        html += '.svgclass { position:absolute; top:0px; left:0px;}'
        html += '</style>'
        return html
       
    def process_info(self):
        self.info = self.coco['info']
    
    def process_licenses(self):
        self.licenses = self.coco['licenses']
    
    def process_categories(self):
        self.categories = {}
        self.super_categories = {}
        for category in self.coco['categories']:
            cat_id = category['id']
            super_category = category['supercategory']
            
            # Add category to the categories dict
            if cat_id not in self.categories:
                self.categories[cat_id] = category
            else:
                print("ERROR: Skipping duplicate category id: {}".format(category))

            # Add category to super_categories dict
            if super_category not in self.super_categories:
                self.super_categories[super_category] = {cat_id} # Create a new set with the category id
            else:
                self.super_categories[super_category] |= {cat_id} # Add category id to the set
                
    def process_images(self):
        self.images = {}
        for image in self.coco['images']:
            image_id = image['id']
            if image_id in self.images:
                print("ERROR: Skipping duplicate image id: {}".format(image))
            else:
                self.images[image_id] = image
                
    def process_segmentations(self):
        self.segmentations = {}
        for segmentation in self.coco['annotations']:
            image_id = segmentation['image_id']
            if image_id not in self.segmentations:
                self.segmentations[image_id] = []
            self.segmentations[image_id].append(segmentation)

In [51]:
annotation_path = '/media/alexey/SSDDataDisk/datasets/walruses/coco/annotations/instances_train2017.json'
image_dir = '/media/alexey/SSDDataDisk/datasets/walruses/coco/images/'

coco_dataset = CocoDataset(annotation_path, image_dir)
# coco_dataset.display_info()
# coco_dataset.display_licenses()
coco_dataset.display_categories()

Categories:
  super_category: animal
    id 1: walrus
    id 2: walrus
    id 3: walrus
    id 4: walrus
    id 5: walrus
    id 6: walrus
    id 7: walrus
    id 8: walrus
    id 9: walrus
    id 10: walrus
    id 11: walrus
    id 12: walrus
    id 13: walrus
    id 14: walrus
    id 15: walrus
    id 16: walrus
    id 17: walrus
    id 18: walrus
    id 19: walrus
    id 20: walrus
    id 21: walrus
    id 22: walrus
    id 23: walrus
    id 24: walrus
    id 25: walrus
    id 26: walrus
    id 27: walrus
    id 28: walrus
    id 29: walrus
    id 30: walrus
    id 31: walrus
    id 32: walrus
    id 33: walrus
    id 34: walrus
    id 35: walrus
    id 36: walrus
    id 37: walrus
    id 38: walrus
    id 39: walrus
    id 40: walrus
    id 41: walrus
    id 42: walrus
    id 43: walrus
    id 44: walrus
    id 45: walrus
    id 46: walrus
    id 47: walrus
    id 48: walrus
    id 49: walrus
    id 50: walrus
    id 51: walrus
    id 52: walrus
    id 53: walrus
    id 54: walrus


    id 5344: walrus
    id 5345: walrus
    id 5346: walrus
    id 5347: walrus
    id 5348: walrus
    id 5349: walrus
    id 5350: walrus
    id 5351: walrus
    id 5352: walrus
    id 5353: walrus
    id 5354: walrus
    id 5355: walrus
    id 5356: walrus
    id 5357: walrus
    id 5358: walrus
    id 5359: walrus
    id 5360: walrus
    id 5361: walrus
    id 5362: walrus
    id 5363: walrus
    id 5364: walrus
    id 5365: walrus
    id 5366: walrus
    id 5367: walrus
    id 5368: walrus
    id 5369: walrus
    id 5370: walrus
    id 5371: walrus
    id 5372: walrus
    id 5373: walrus
    id 5374: walrus
    id 5375: walrus
    id 5376: walrus
    id 5377: walrus
    id 5378: walrus
    id 5379: walrus
    id 5380: walrus
    id 5381: walrus
    id 5382: walrus
    id 5383: walrus
    id 5384: walrus
    id 5385: walrus
    id 5386: walrus
    id 5387: walrus
    id 5388: walrus
    id 5389: walrus
    id 5390: walrus
    id 5391: walrus
    id 5392: walrus
    id 5393: walrus


    id 9483: walrus
    id 9484: walrus
    id 9485: walrus
    id 9486: walrus
    id 9487: walrus
    id 9488: walrus
    id 9489: walrus
    id 9490: walrus
    id 9491: walrus
    id 9492: walrus
    id 9493: walrus
    id 9494: walrus
    id 9495: walrus
    id 9496: walrus
    id 9497: walrus
    id 9498: walrus
    id 9499: walrus
    id 9500: walrus
    id 9501: walrus
    id 9502: walrus
    id 9503: walrus
    id 9504: walrus
    id 9505: walrus
    id 9506: walrus
    id 9507: walrus
    id 9508: walrus
    id 9509: walrus
    id 9510: walrus
    id 9511: walrus
    id 9512: walrus
    id 9513: walrus
    id 9514: walrus
    id 9515: walrus
    id 9516: walrus
    id 9517: walrus
    id 9518: walrus
    id 9519: walrus
    id 9520: walrus
    id 9521: walrus
    id 9522: walrus
    id 9523: walrus
    id 9524: walrus
    id 9525: walrus
    id 9526: walrus
    id 9527: walrus
    id 9528: walrus
    id 9529: walrus
    id 9530: walrus
    id 9531: walrus
    id 9532: walrus


    id 14346: walrus
    id 14347: walrus
    id 14348: walrus
    id 14349: walrus
    id 14350: walrus
    id 14351: walrus
    id 14352: walrus
    id 14353: walrus
    id 14354: walrus
    id 14355: walrus
    id 14356: walrus
    id 14357: walrus
    id 14358: walrus
    id 14359: walrus
    id 14360: walrus
    id 14361: walrus
    id 14362: walrus
    id 14363: walrus
    id 14364: walrus
    id 14365: walrus
    id 14366: walrus
    id 14367: walrus
    id 14368: walrus
    id 14369: walrus
    id 14370: walrus
    id 14371: walrus
    id 14372: walrus
    id 14373: walrus
    id 14374: walrus
    id 14375: walrus
    id 14376: walrus
    id 14377: walrus
    id 14378: walrus
    id 14379: walrus
    id 14380: walrus
    id 14381: walrus
    id 14382: walrus
    id 14383: walrus
    id 14384: walrus
    id 14385: walrus
    id 14386: walrus
    id 14387: walrus
    id 14388: walrus
    id 14389: walrus
    id 14390: walrus
    id 14391: walrus
    id 14392: walrus
    id 14393:

    id 19466: walrus
    id 19467: walrus
    id 19468: walrus
    id 19469: walrus
    id 19470: walrus
    id 19471: walrus
    id 19472: walrus
    id 19473: walrus
    id 19474: walrus
    id 19475: walrus
    id 19476: walrus
    id 19477: walrus
    id 19478: walrus
    id 19479: walrus
    id 19480: walrus
    id 19481: walrus
    id 19482: walrus
    id 19483: walrus
    id 19484: walrus
    id 19485: walrus
    id 19486: walrus
    id 19487: walrus
    id 19488: walrus
    id 19489: walrus
    id 19490: walrus
    id 19491: walrus
    id 19492: walrus
    id 19493: walrus
    id 19494: walrus
    id 19495: walrus
    id 19496: walrus
    id 19497: walrus
    id 19498: walrus
    id 19499: walrus
    id 19500: walrus
    id 19501: walrus
    id 19502: walrus
    id 19503: walrus
    id 19504: walrus
    id 19505: walrus
    id 19506: walrus
    id 19507: walrus
    id 19508: walrus
    id 19509: walrus
    id 19510: walrus
    id 19511: walrus
    id 19512: walrus
    id 19513:

...

    id 196508: walrus
    id 196509: walrus
    id 196510: walrus
    id 196511: walrus
    id 196512: walrus
    id 196513: walrus
    id 196514: walrus
    id 196515: walrus
    id 196516: walrus
    id 196517: walrus
    id 196518: walrus
    id 196519: walrus
    id 196520: walrus
    id 196521: walrus
    id 196522: walrus
    id 196523: walrus
    id 196524: walrus
    id 196525: walrus
    id 196526: walrus
    id 196527: walrus
    id 196528: walrus
    id 196529: walrus
    id 196530: walrus
    id 196531: walrus
    id 196532: walrus
    id 196533: walrus
    id 196534: walrus
    id 196535: walrus
    id 196536: walrus
    id 196537: walrus
    id 196538: walrus
    id 196539: walrus
    id 196540: walrus
    id 196541: walrus
    id 196542: walrus
    id 196543: walrus
    id 196544: walrus
    id 196545: walrus
    id 196546: walrus
    id 196547: walrus
    id 196548: walrus
    id 196549: walrus
    id 196550: walrus
    id 196551: walrus
    id 196552: walrus
    id 196

    id 201335: walrus
    id 201336: walrus
    id 201337: walrus
    id 201338: walrus
    id 201339: walrus
    id 201340: walrus
    id 201341: walrus
    id 201342: walrus
    id 201343: walrus
    id 201344: walrus
    id 201345: walrus
    id 201346: walrus
    id 201347: walrus
    id 201348: walrus
    id 201349: walrus
    id 201350: walrus
    id 201351: walrus
    id 201352: walrus
    id 201353: walrus
    id 201354: walrus
    id 201355: walrus
    id 201356: walrus
    id 201357: walrus
    id 201358: walrus
    id 201359: walrus
    id 201360: walrus
    id 201361: walrus
    id 201362: walrus
    id 201363: walrus
    id 201364: walrus
    id 201365: walrus
    id 201366: walrus
    id 201367: walrus
    id 201368: walrus
    id 201369: walrus
    id 201370: walrus
    id 201371: walrus
    id 201372: walrus
    id 201373: walrus
    id 201374: walrus
    id 201375: walrus
    id 201376: walrus
    id 201377: walrus
    id 201378: walrus
    id 201379: walrus
    id 201

    id 206232: walrus
    id 206233: walrus
    id 206234: walrus
    id 206235: walrus
    id 206236: walrus
    id 206237: walrus
    id 206238: walrus
    id 206239: walrus
    id 206240: walrus
    id 206241: walrus
    id 206242: walrus
    id 206243: walrus
    id 206244: walrus
    id 206245: walrus
    id 206246: walrus
    id 206247: walrus
    id 206248: walrus
    id 206249: walrus
    id 206250: walrus
    id 206251: walrus
    id 206252: walrus
    id 206253: walrus
    id 206254: walrus
    id 206255: walrus
    id 206256: walrus
    id 206257: walrus
    id 206258: walrus
    id 206259: walrus
    id 206260: walrus
    id 206261: walrus
    id 206262: walrus
    id 206263: walrus
    id 206264: walrus
    id 206265: walrus
    id 206266: walrus
    id 206267: walrus
    id 206268: walrus
    id 206269: walrus
    id 206270: walrus
    id 206271: walrus
    id 206272: walrus
    id 206273: walrus
    id 206274: walrus
    id 206275: walrus
    id 206276: walrus
    id 206

    id 211574: walrus
    id 211575: walrus
    id 211576: walrus
    id 211577: walrus
    id 211578: walrus
    id 211579: walrus
    id 211580: walrus
    id 211581: walrus
    id 211582: walrus
    id 211583: walrus
    id 211584: walrus
    id 211585: walrus
    id 211586: walrus
    id 211587: walrus
    id 211588: walrus
    id 211589: walrus
    id 211590: walrus
    id 211591: walrus
    id 211592: walrus
    id 211593: walrus
    id 211594: walrus
    id 211595: walrus
    id 211596: walrus
    id 211597: walrus
    id 211598: walrus
    id 211599: walrus
    id 211600: walrus
    id 211601: walrus
    id 211602: walrus
    id 211603: walrus
    id 211604: walrus
    id 211605: walrus
    id 211606: walrus
    id 211607: walrus
    id 211608: walrus
    id 211609: walrus
    id 211610: walrus
    id 211611: walrus
    id 211612: walrus
    id 211613: walrus
    id 211614: walrus
    id 211615: walrus
    id 211616: walrus
    id 211617: walrus
    id 211618: walrus
    id 211

    id 216310: walrus
    id 216311: walrus
    id 216312: walrus
    id 216313: walrus
    id 216314: walrus
    id 216315: walrus
    id 216316: walrus
    id 216317: walrus
    id 216318: walrus
    id 216319: walrus
    id 216320: walrus
    id 216321: walrus
    id 216322: walrus
    id 216323: walrus
    id 216324: walrus
    id 216325: walrus
    id 216326: walrus
    id 216327: walrus
    id 216328: walrus
    id 216329: walrus
    id 216330: walrus
    id 216331: walrus
    id 216332: walrus
    id 216333: walrus
    id 216334: walrus
    id 216335: walrus
    id 216336: walrus
    id 216337: walrus
    id 216338: walrus
    id 216339: walrus
    id 216340: walrus
    id 216341: walrus
    id 216342: walrus
    id 216343: walrus
    id 216344: walrus
    id 216345: walrus
    id 216346: walrus
    id 216347: walrus
    id 216348: walrus
    id 216349: walrus
    id 216350: walrus
    id 216351: walrus
    id 216352: walrus
    id 216353: walrus
    id 216354: walrus
    id 216

In [58]:
html = coco_dataset.display_image('random', use_url=False)

with open('viz.html', 'w') as f:
    f.write(html)

IPython.display.HTML(html)

Image:
  license: 1
  file_name: 1425.jpg
  coco_url: 
  height: 700
  width: 700
  date_captured: 
  flickr_url: 
  id: 1425
  segmentations (5):
    33387:blue:{'id': 1, 'name': 'walrus', 'supercategory': 'animal'}
    33388:purple:{'id': 1, 'name': 'walrus', 'supercategory': 'animal'}
    33389:red:{'id': 1, 'name': 'walrus', 'supercategory': 'animal'}
    33390:green:{'id': 1, 'name': 'walrus', 'supercategory': 'animal'}
    33391:orange:{'id': 1, 'name': 'walrus', 'supercategory': 'animal'}
